In [1]:
import os
import json
import argparse
import numpy as np
from model import build_model, save_weights

In [2]:
DATA_DIR = './data'

BATCH_SIZE = 16
SEQ_LENGTH = 64

class TrainLogger(object):
    def __init__(self, file):
        self.file = os.path.join(LOG_DIR, file)
        self.epochs = 0
        with open(self.file, 'w') as f:
            f.write('epoch,loss,acc\n')

    def add_entry(self, loss, acc):
        self.epochs += 1
        s = '{},{},{}\n'.format(self.epochs, loss, acc)
        with open(self.file, 'a') as f:
            f.write(s)

def read_batches(T, vocab_size):
    length = T.shape[0];
    b_chars = int(length / BATCH_SIZE); 
    for start in range(0, b_chars - SEQ_LENGTH, SEQ_LENGTH):
        X = np.zeros((BATCH_SIZE, SEQ_LENGTH))
        Y = np.zeros((BATCH_SIZE, SEQ_LENGTH, vocab_size))
        for b_idx in range(0, BATCH_SIZE): 
            for i in range(0, SEQ_LENGTH):
                X[b_idx, i] = T[b_chars * b_idx + start + i] 
                Y[b_idx, i, T[b_chars * b_idx + start + i + 1]] = 1
        yield X, Y

In [3]:
def train_model(input_text, epochs=100, save_frequency=10):
    char_to_idx = { ch: i for (i, ch) in enumerate(sorted(list(set(input_text)))) }
    with open(os.path.join(DATA_DIR, 'char_to_idx.json'), 'w') as f:
        json.dump(char_to_idx, f)
    idx_to_char = { i: ch for (ch, i) in char_to_idx.items() }
    vocab_size = len(char_to_idx)
    model = build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size)
    model.summary()
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    T = np.asarray([char_to_idx[c] for c in input_text], dtype=np.int32) 
    print("Length of input_text:" + str(T.size)) 
    steps_per_epoch = (len(input_text) / BATCH_SIZE - 1) / SEQ_LENGTH  
    log = TrainLogger('training_log.csv')
    
    for epoch in range(epochs):
        print('\nEpoch {}/{}'.format(epoch + 1, epochs))        
        losses, accs = [], []
        for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
            loss, acc = model.train_on_batch(X, Y)
            print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
            losses.append(loss)
            accs.append(acc)
        
        log.add_entry(np.average(losses), np.average(accs))
        
        if (epoch + 1) % save_frequency == 0:
            save_weights(epoch + 1, model)
            print('Saved checkpoint', 'weights.{}.h5'.format(epoch + 1))

In [6]:
if __name__ == '__main__':
    parser = argparse.ArgumentParser()
    parser.add_argument('--input', default='input.txt')
    parser.add_argument('--epochs', type=int, default=100)
    parser.add_argument('--freq', type=int, default=10)
    parser.add_argument('-f')
    args = parser.parse_args()

    train_model(open(os.path.join(DATA_DIR, args.input)).read(), args.epochs, args.freq)

Number of unique characters: 86
Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (16, 64, 512)             44032     
_________________________________________________________________
lstm (LSTM)                  (16, 64, 256)             787456    
_________________________________________________________________
dropout (Dropout)            (16, 64, 256)             0         
_________________________________________________________________
lstm_1 (LSTM)                (16, 64, 256)             525312    
_________________________________________________________________
dropout_1 (Dropout)          (16, 64, 256)             0         
_________________________________________________________________
lstm_2 (LSTM)                (16, 64, 256)             525312    
_________________________________________________________________
dropout_2 (Dropout)     

Batch 27: loss = 3.2046315670013428, acc = 0.1943359375
[[29.  1.  3. ... 28. 84.  3.]
 [63. 84.  3. ... 18.  1.  3.]
 [ 3. 34.  3. ... 31.  3. 63.]
 ...
 [28. 33. 31. ...  3. 34. 18.]
 [61. 60. 84. ... 60. 84.  3.]
 [84.  3. 30. ... 34. 70.  3.]]
Batch 28: loss = 3.2938833236694336, acc = 0.1748046875
[[28.  3. 62. ...  3. 28.  3.]
 [34.  3. 61. ...  3. 31.  3.]
 [61. 61.  1. ... 25. 40. 66.]
 ...
 [ 1.  3. 29. ...  3. 29. 60.]
 [31.  3. 61. ...  1.  3. 28.]
 [64. 17. 34. ... 61. 60. 29.]]
Batch 29: loss = 3.4244043827056885, acc = 0.15625
[[58. 62. 60. ... 25. 33. 72.]
 [63. 17. 64. ...  1. 46. 72.]
 [68. 62.  1. ... 28. 84.  3.]
 ...
 [28.  1.  3. ...  0.  3. 32.]
 [22.  3. 29. ... 17. 33. 84.]
 [ 1. 28. 34. ... 65. 58. 70.]]
Batch 30: loss = 3.3749380111694336, acc = 0.1533203125
[[75. 70. 58. ... 17. 29. 14.]
 [ 1. 29. 69. ... 33.  0. 40.]
 [34.  3. 29. ...  3. 34.  3.]
 ...
 [70.  3. 29. ... 34. 84.  3.]
 [ 3. 34.  3. ... 28.  3. 32.]
 [ 1. 40. 78. ... 84.  3. 28.]]
Batch 31: los

Batch 61: loss = 3.1667962074279785, acc = 0.1640625
[[ 3. 34.  3. ... 31. 22.  3.]
 [14. 23.  0. ... 26. 29. 28.]
 [ 3. 31.  3. ...  1. 61. 62.]
 ...
 [84.  0.  3. ... 23. 22.  0.]
 [ 7. 58.  1. ... 51. 25.  1.]
 [29. 34.  1. ... 28.  1. 62.]]
Batch 62: loss = 3.074394702911377, acc = 0.181640625
[[28. 29. 28. ... 64.  0.  5.]
 [84.  0.  3. ... 25.  0. 58.]
 [63. 84.  3. ... 61.  0.  5.]
 ...
 [47. 25. 47. ... 65. 58. 70.]
 [18. 15. 24. ... 45. 72. 80.]
 [28. 62. 84. ... 84. 62. 17.]]
Batch 63: loss = 3.2588791847229004, acc = 0.1494140625
[[ 1. 41. 72. ...  3. 61. 17.]
 [84.  3. 31. ...  1. 59. 58.]
 [ 1. 41. 72. ... 31. 33. 28.]
 ...
 [ 1. 40. 78. ... 34.  3. 64.]
 [62.  0. 40. ... 61. 60. 84.]
 [61.  1. 64. ...  3. 28. 70.]]
Batch 64: loss = 3.2006144523620605, acc = 0.1552734375
[[59.  1. 59. ... 64.  1. 64.]
 [64. 84.  3. ... 66. 64.  0.]
 [84.  3. 31. ...  3. 31.  3.]
 ...
 [17. 34.  1. ... 30.  3. 32.]
 [ 0.  3. 34. ...  3. 30.  3.]
 [ 3. 62. 17. ...  0.  0. 51.]]
Batch 65: los

Batch 95: loss = 2.927380084991455, acc = 0.2041015625
[[34.  1.  3. ... 17. 61.  1.]
 [63. 84.  3. ... 28. 17. 63.]
 [72. 80. 75. ...  1. 45. 72.]
 ...
 [58. 17. 28. ... 18.  0. 47.]
 [ 3. 31.  3. ... 25.  1. 18.]
 [28. 61. 63. ... 71. 68. 76.]]
Batch 96: loss = 2.9266724586486816, acc = 0.201171875
[[ 3. 28. 70. ... 62. 63. 84.]
 [84.  3. 28. ... 56. 61. 62.]
 [80. 62.  0. ... 84.  3. 34.]
 ...
 [25. 46. 70. ... 14. 23.  0.]
 [16. 21.  0. ...  1. 73.  1.]
 [ 1. 72. 63. ... 14. 35. 37.]]
Batch 97: loss = 2.9982175827026367, acc = 0.1875
[[64. 17. 64. ...  3. 31. 22.]
 [ 1. 58. 17. ... 17. 63.  1.]
 [70.  3. 61. ... 61. 17. 60.]
 ...
 [38. 25. 31. ...  1.  3. 28.]
 [16. 18. 19. ...  1. 32. 17.]
 [33.  0. 40. ...  3. 29. 61.]]
Batch 98: loss = 2.967397451400757, acc = 0.21484375
[[ 3. 28. 33. ... 32. 84.  3.]
 [63. 62. 63. ... 61. 18.  1.]
 [84.  3. 34. ...  1. 63. 62.]
 ...
 [22.  3. 34. ... 29.  0. 84.]
 [60. 84.  3. ...  3. 29. 18.]
 [61.  1.  3. ...  3. 33. 32.]]
Batch 99: loss = 2.

Batch 3: loss = 2.8299379348754883, acc = 0.2236328125
[[58. 64. 26. ...  3. 28. 22.]
 [30.  3. 62. ...  1. 17. 18.]
 [28. 84.  3. ...  3. 31. 70.]
 ...
 [30.  3. 60. ... 34. 32.  1.]
 [ 3. 31.  3. ... 64. 63. 62.]
 [43. 65. 66. ...  3. 60. 17.]]
Batch 4: loss = 2.714509963989258, acc = 0.2470703125
[[ 3. 60. 29. ...  3. 31.  3.]
 [ 0. 47. 25. ... 75. 66. 64.]
 [ 3. 58. 18. ... 62. 62. 63.]
 ...
 [33. 32. 31. ... 56. 34. 17.]
 [84.  3. 28. ... 61.  1.  3.]
 [29.  1.  3. ...  3. 61. 29.]]
Batch 5: loss = 2.7252750396728516, acc = 0.2587890625
[[61. 18.  1. ...  1. 29. 58.]
 [64. 76. 11. ... 28. 22.  3.]
 [84.  3. 30. ...  3. 30.  3.]
 ...
 [32.  1.  3. ... 28. 29. 60.]
 [29. 70.  3. ... 17. 62. 84.]
 [34.  1.  3. ... 70.  3. 62.]]
Batch 6: loss = 2.8527474403381348, acc = 0.240234375
[[75. 80. 62. ...  3. 28. 17.]
 [62. 17. 60. ... 29. 60. 84.]
 [62. 17. 61. ... 62.  1. 35.]
 ...
 [84.  3. 32. ... 28. 70.  3.]
 [ 3. 31.  3. ... 58. 77. 58.]
 [60. 28. 84. ... 31. 17. 29.]]
Batch 7: loss 

...

Batch 93: loss = 0.22588038444519043, acc = 0.9248046875
[[28. 34. 84. ...  5.  1. 41.]
 [71. 64. 65. ... 25. 28.  0.]
 [25. 84.  0. ... 58. 17. 63.]
 ...
 [62. 61.  1. ... 61. 29. 28.]
 [32. 70.  3. ... 63. 17. 58.]
 [61. 84.  0. ... 84. 63. 62.]]
Batch 94: loss = 0.23476366698741913, acc = 0.91796875
[[72. 77. 77. ...  3. 34. 17.]
 [28. 84.  3. ...  1. 61. 17.]
 [ 1.  3. 30. ... 71.  1. 43.]
 ...
 [84.  3. 31. ... 28. 22.  3.]
 [ 1. 58. 63. ... 63. 84.  0.]
 [61.  1. 56. ... 61. 63.  1.]]
Batch 95: loss = 0.22669807076454163, acc = 0.927734375
[[34.  1.  3. ... 17. 61.  1.]
 [63. 84.  3. ... 28. 17. 63.]
 [72. 80. 75. ...  1. 45. 72.]
 ...
 [58. 17. 28. ... 18.  0. 47.]
 [ 3. 31.  3. ... 25.  1. 18.]
 [28. 61. 63. ... 71. 68. 76.]]
Batch 96: loss = 0.25980186462402344, acc = 0.912109375
[[ 3. 28. 70. ... 62. 63. 84.]
 [84.  3. 28. ... 56. 61. 62.]
 [80. 62.  0. ... 84.  3. 34.]
 ...
 [25. 46. 70. ... 14. 23.  0.]
 [16. 21.  0. ...  1. 73.  1.]
 [ 1. 72. 63. ... 14. 35. 37.]]
Batch 97

Batch 126: loss = 0.22445744276046753, acc = 0.931640625

Epoch 100/100
[[51. 25.  1. ... 28.  0. 40.]
 [84. 29. 61. ... 29.  1. 34.]
 [47. 75. 58. ... 32. 33.  1.]
 ...
 [ 3. 29. 17. ... 22.  0. 47.]
 [22.  3. 28. ... 28. 84.  3.]
 [ 3. 33. 17. ...  3. 31.  3.]]
Batch 1: loss = 0.29189497232437134, acc = 0.900390625
[[25. 21. 14. ...  3. 28.  3.]
 [29. 61. 84. ...  1. 31. 33.]
 [28. 17. 34. ... 64. 84.  3.]
 ...
 [25. 41. 72. ... 78. 76. 66.]
 [31.  3. 63. ...  3. 28.  3.]
 [61. 17. 63. ...  0. 47. 25.]]
Batch 2: loss = 0.23042380809783936, acc = 0.9287109375
[[62. 60. 60. ... 60. 62.  1.]
 [28. 84.  0. ... 29. 84.  3.]
 [30.  3. 64. ...  1. 29. 17.]
 ...
 [60.  1. 31. ... 30.  0.  3.]
 [60. 17. 60. ... 17. 61. 84.]
 [50. 58. 68. ... 66. 58.  1.]]
Batch 3: loss = 0.2467598021030426, acc = 0.9140625
[[58. 64. 26. ...  3. 28. 22.]
 [30.  3. 62. ...  1. 17. 18.]
 [28. 84.  3. ...  3. 31. 70.]
 ...
 [30.  3. 60. ... 34. 32.  1.]
 [ 3. 31.  3. ... 64. 63. 62.]
 [43. 65. 66. ...  3. 60. 17.

Batch 34: loss = 0.24541699886322021, acc = 0.921875
[[31. 30. 84. ... 17. 63.  1.]
 [30. 14. 62. ...  3. 28. 70.]
 [29.  1.  3. ... 66. 75. 60.]
 ...
 [ 1.  3. 32. ... 84.  3. 28.]
 [69. 66. 71. ... 34.  3. 29.]
 [53. 16.  3. ... 50. 66. 63.]]
Batch 35: loss = 0.2092885971069336, acc = 0.9189453125
[[63. 62. 63. ... 17. 62. 84.]
 [ 3.  1. 28. ...  3. 34. 22.]
 [69. 62.  1. ... 79. 66. 58.]
 ...
 [ 3. 60. 62. ...  1. 31. 32.]
 [18.  1. 61. ...  3. 62. 17.]
 [62.  0.  5. ... 25. 21. 14.]]
Batch 36: loss = 0.19578447937965393, acc = 0.935546875
[[84.  0. 38. ... 61. 60. 84.]
 [ 3.  1. 62. ...  0. 51. 25.]
 [ 1. 43. 65. ... 17. 33.  1.]
 ...
 [33. 84.  3. ... 18.  1. 12.]
 [28.  1. 29. ... 64. 17. 61.]
 [23.  0. 38. ... 32. 22.  3.]]
Batch 37: loss = 0.20462515950202942, acc = 0.9375
[[ 0. 43. 25. ... 60.  1. 31.]
 [ 1. 17. 23. ...  1. 16.  1.]
 [34. 33. 32. ...  3. 31. 22.]
 ...
 [29. 17. 32. ...  3. 28.  3.]
 [ 1. 62. 17. ... 28. 21. 12.]
 [32. 17. 32. ... 17. 84. 84.]]
Batch 38: loss =

Batch 68: loss = 0.24604907631874084, acc = 0.9150390625
[[58. 76. 62. ... 32. 18.  1.]
 [ 3. 34.  3. ... 60. 29. 28.]
 [77. 66. 71. ... 38. 25. 31.]
 ...
 [66. 71. 64. ... 17. 84.  3.]
 [62. 61. 84. ... 62. 61.  1.]
 [28. 84.  3. ...  3. 29. 18.]]
Batch 69: loss = 0.22314909100532532, acc = 0.921875
[[29. 17. 28. ... 30.  3. 34.]
 [84.  3. 31. ... 63. 64. 25.]
 [ 0. 29. 84. ... 84. 63. 62.]
 ...
 [31.  3. 58. ...  3. 31.  3.]
 [61. 17. 25. ... 31.  3. 31.]
 [ 1. 29. 60. ... 25. 84.  0.]]
Batch 70: loss = 0.25689107179641724, acc = 0.908203125
[[17. 33. 84. ... 28. 18.  1.]
 [84.  0.  1. ... 76. 66. 60.]
 [61.  1. 28. ...  3. 28. 60.]
 ...
 [58. 59. 58. ... 58. 59. 58.]
 [33. 28.  1. ... 47. 25. 47.]
 [ 0.  0. 51. ... 58. 75. 75.]]
Batch 71: loss = 0.21594950556755066, acc = 0.92578125
[[60. 17. 29. ... 72. 77. 77.]
 [ 1. 31. 58. ... 61. 84.  3.]
 [60.  1. 60. ... 61. 18.  1.]
 ...
 [ 1.  3. 28. ... 60. 29. 84.]
 [58. 70.  7. ... 28. 29.  0.]
 [ 1. 43. 65. ... 29. 84.  3.]]
Batch 72: l

Batch 102: loss = 0.24262331426143646, acc = 0.9169921875
[[ 0. 28. 84. ... 33.  1.  3.]
 [34. 33. 84. ...  1. 61. 62.]
 [ 1. 40. 78. ... 60. 62.  1.]
 ...
 [64. 63.  1. ... 62.  0.  5.]
 [ 3. 61. 63. ...  1. 40. 78.]
 [ 0. 46. 25. ... 28.  3. 62.]]
Batch 103: loss = 0.24004745483398438, acc = 0.9248046875
[[34.  3. 34. ... 62. 17. 61.]
 [63. 84.  3. ... 84.  3. 32.]
 [ 3. 31. 70. ... 28. 60. 62.]
 ...
 [ 1. 41. 72. ... 38. 25. 28.]
 [76. 66. 60. ... 28. 28.  1.]
 [63. 58.  1. ... 84.  3. 31.]]
Batch 104: loss = 0.21933677792549133, acc = 0.921875
[[84.  3. 28. ... 29. 60. 84.]
 [70.  3. 32. ... 17. 28. 84.]
 [ 1.  3. 31. ... 18.  1. 12.]
 ...
 [ 0. 43. 25. ... 28. 17. 28.]
 [60. 28. 28. ... 29. 29.  1.]
 [ 3. 62. 63. ...  3. 28. 28.]]
Batch 105: loss = 0.20211675763130188, acc = 0.921875
[[ 3. 31.  3. ... 58. 59. 58.]
 [ 3. 34.  3. ... 47. 65. 62.]
 [28. 17. 84. ...  1. 28. 64.]
 ...
 [ 1. 28. 34. ...  1. 60. 61.]
 [ 3. 28.  3. ...  3. 31.  3.]
 [28. 84.  3. ...  3. 28. 18.]]
Batch 10